In [1]:
import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings("ignore")
from sklearn.model_selection import train_test_split
from sklearn.decomposition import PCA
import random
import keras
from keras.models import Sequential,Model
from keras.layers import Dense, Activation, Flatten, Convolution1D, Dropout,Input,BatchNormalization,MaxPooling1D,concatenate
from keras.utils import np_utils,multi_gpu_model
from keras.callbacks import ModelCheckpoint
from keras import regularizers
from sklearn.cluster import KMeans
from scipy import stats
from sklearn import preprocessing
from keras import backend as bek
import gc
%matplotlib inline

Using TensorFlow backend.


In [2]:
"""
data cell
"""
df1=pd.read_csv('/home/dp/Desktop/Bit/datapath/pair_end_merge_SYS_random_400_split_up.csv',index_col=0)## SYS
#df1=pd.read_csv('/home/dp/Desktop/Bit/datapath/pair_end_merge_DIA_random_400_split_down.csv',index_col=0)# DIA


In [3]:
for i,item in enumerate(df1['SYS']):
    '''
    Repleace SYS by DIA when you run diastolic
    '''
    if(df1['time'].iloc[i]==2):
        continue
    elif(df1['time'].iloc[i]==1):
        temp=df1[(df1['Person No']==df1['Person No'].iloc[i])&(df1['time']==2)]['SYS']
        if(temp.empty):
            continue
        else:
            print(df1['SYS'].iloc[i],temp.iloc[0])
            df1['SYS'].iloc[i]=temp.iloc[0]
    else:
        continue

124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
124.0 102.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.0 147.0
140.

In [4]:
cond2 = df1['count']!=0
df1 = df1[cond2]

#normalize
target = 'SYS'# DIA

In [5]:
'''
model cell
'''
def base_model():
    in_s = Input((406, 1))
    model_s = Convolution1D(nb_filter=256, filter_length=3) (in_s)
    model_s = BatchNormalization(axis=-1)(model_s)
    model_s = Activation('relu')(model_s)
    model_s = MaxPooling1D(pool_size=2)(model_s)
    
    model_s = Convolution1D(nb_filter=256, filter_length=3) (model_s)
    model_s = BatchNormalization(axis=-1)(model_s)
    model_s = Activation('relu')(model_s)
    model_s = MaxPooling1D(pool_size=2)(model_s)
    
    model_s = Convolution1D(nb_filter=512, filter_length=3) (model_s)
    model_s = BatchNormalization(axis=-1)(model_s)
    model_s = Activation('relu')(model_s)
    model_s = MaxPooling1D(pool_size=2)(model_s)
    
    model_s = Convolution1D(nb_filter=1024, filter_length=3) (model_s)
    model_s = BatchNormalization(axis=-1)(model_s)
    model_s = Activation('relu')(model_s)
    model_s = MaxPooling1D(pool_size=2)(model_s)
    
    model_s = Convolution1D(nb_filter=2048, filter_length=3) (model_s)
    model_s = BatchNormalization(axis=-1)(model_s)
    model_s = Activation('relu')(model_s)
    model_s = MaxPooling1D(pool_size=2)(model_s)
    
    model_s = Flatten()(model_s)
    
    '''
    input1 = keras.layers.Input(shape=(1,))
    c = keras.layers.Concatenate(axis=-1)([model_s, input1])
    '''
    m = BatchNormalization(axis=-1)(model_s)
    m = Dense(4096,activation='relu')(m)
    m = Dense(2048,activation='relu')(m)
    out = Dense(1,activation='linear')(m)
    
    model = Model(inputs=[in_s], outputs=[out])
    
    adam=keras.optimizers.Adam(lr=0.00001, beta_1=0.9, beta_2=0.999)
    model = multi_gpu_model(model,gpus=6)
    model.compile(loss='mean_squared_error', optimizer='adam')
    return model

In [6]:
def test_step(train_temp,test_temp):
    X_train_s = train_temp.iloc[:,17:423]
    X_test_s = test_temp.iloc[:,17:423]
    '''
    Replace all SYS by DIA for running DIA or diastolic condition
    '''
    
    f1=['SYS']
    Y_train = train_temp[f1]
    Y_train = scalert.transform(Y_train)
    
    # reshape train data
    X_train_r_s = np.zeros((len(X_train_s), 406, 1))
    X_train_r_s[:, :, 0] = X_train_s

    # reshape vali data
    X_test_r_s = np.zeros((len(X_test_s), 406, 1))
    X_test_r_s[:, :, 0] = X_test_s
    

    
    #fit
    filepath="weights_best.hdf5"
    checkpoint = ModelCheckpoint(filepath, monitor='loss', verbose=1, save_best_only=True,mode='min')
    callbacks_list = [checkpoint]
    
    model= base_model()
    model.fit([X_train_r_s], Y_train, epochs=1000, batch_size=3000,callbacks=callbacks_list,verbose=2)

    
    test_pred = model.predict([X_test_r_s])
    test_pred1 = scalert.inverse_transform(test_pred)
    test_temp['SYS_p']=test_pred1
    
    temp_a=0
    temp_b=0
    test_SYS_r=[]
    test_SYS_p=[]

    
    for i,item in enumerate(test_temp['Person No']):
        if((test_temp['Person No'].iloc[i]!=temp_a) | (test_temp['time'].iloc[i]!=temp_b)):
            
            #administrator mode
            test_SYS_r.append(test_temp['SYS'].iloc[i])
            temp = test_temp[(test_temp['Person No']==test_temp['Person No'].iloc[i])&(test_temp['time']==test_temp['time'].iloc[i])]
            t = np.median(temp['SYS_p'])
            test_SYS_p.append(t)
            temp_a = test_temp['Person No'].iloc[i]
            temp_b = test_temp['time'].iloc[i]

            
    print(test_SYS_p)
    print(test_SYS_r)
    del model
    bek.clear_session()
    gc.collect()
    return (test_SYS_p,test_SYS_r)

In [7]:
def test_step1(train_temp,test_temp):
    X_train_s = train_temp.iloc[:,17:423]
    X_test_s = test_temp.iloc[:,17:423]
    '''
    Note: Replace SYS by DIA when you run DIA
    '''
    
    f1=['SYS']
    Y_train = train_temp[f1]
    Y_train = scalert.transform(Y_train)
    
    # reshape train data
    X_train_r_s = np.zeros((len(X_train_s), 406, 1))
    X_train_r_s[:, :, 0] = X_train_s

    # reshape vali data
    X_test_r_s = np.zeros((len(X_test_s), 406, 1))
    X_test_r_s[:, :, 0] = X_test_s
    

    #fit
    
    model1=base_model()
    model1.load_weights('weights_best.hdf5', by_name = True)

    
    test_pred = model1.predict([X_test_r_s])
    test_pred1 = scalert.inverse_transform(test_pred)
    test_temp['SYS_p']=test_pred1
    
    temp_a=0
    temp_b=0
    test_SYS_r=[]
    test_SYS_p=[]

    
    for i,item in enumerate(test_temp['Person No']):
        if((test_temp['Person No'].iloc[i]!=temp_a) | (test_temp['time'].iloc[i]!=temp_b)):
            
            #administrator mode
            test_SYS_r.append(test_temp['SYS'].iloc[i])
            temp = test_temp[(test_temp['Person No']==test_temp['Person No'].iloc[i])&(test_temp['time']==test_temp['time'].iloc[i])]
            t = np.median(temp['SYS_p'])
            test_SYS_p.append(t)
            temp_a = test_temp['Person No'].iloc[i]
            temp_b = test_temp['time'].iloc[i]

            
    print(test_SYS_p)
    print(test_SYS_r)
    
    del model1
    bek.clear_session()
    gc.collect()
    
    return (test_SYS_p,test_SYS_r)

In [8]:
################
#testingNo_all = [689]
################
#1273,543,1002,1831,2439,1101,756,1074,1145,342,245,149,1888,1373,1020,1775,1598,1436,2095,2096,1722,2390,1483,2204,2102,2203,1390,65,2101
testingNo_all = [1273,543,1002,342,245,149,1888,1373,1020,1775,1598, 1436, 1722, 2095, 2096]# Added by me

'''
Note: Repace all SYS in this cell by DIA when you run DIA
'''
for testingNo in testingNo_all:

    test_p=[]
    test_r=[]
    
    test_p_best=[]
    test_r_best=[]
    
    for test_time in range(10,16):
        test  = df1[(df1['count']==testingNo)&(df1['count_time']==test_time)]
        if(test.empty):
            continue
        else:
            
            test_index = test.index
            data_base = df1.drop(test_index)
            t = data_base[target]
            t = t.values.reshape(-1, 1)
            scalert = preprocessing.MinMaxScaler().fit(t)
            
            train = df1[(df1['count']==testingNo)&(df1['count_time']<test_time)&(df1['count_time']>(test_time-9))]
            
            (temp_pred,temp_real) = test_step(train,test)
            (temp_pred_best,temp_real_best) = test_step1(train,test)
            
            test_p.append(temp_pred)
            test_r.append(temp_real)
            
            test_p_best.append(temp_pred_best)
            test_r_best.append(temp_real_best)
            
    d = {'SYS_real': test_r, 'SYS_pred': test_p}
    df_f = pd.DataFrame(data = d)
    
    ind =[]
    for j in range(3,len(df_f.index)+3):
        ind.append(j)
    
    df_f.index=ind
    
    name_temp =str(testingNo)+'-1000-256.csv'
    df_f.to_csv(name_temp)
    
    
    d_best = {'SYS_real': test_r_best, 'SYS_pred': test_p_best}
    df_f_best = pd.DataFrame(data = d_best)
    
    ind =[]
    for j in range(3,len(df_f_best.index)+3):
        ind.append(j)
    
    df_f_best.index=ind
    
    name_temp_best =str(testingNo)+'-1000-256-best.csv'
    df_f_best.to_csv(name_temp_best)

Epoch 1/1000
 - 27s - loss: 3.1276

Epoch 00001: loss improved from inf to 3.12757, saving model to weights_best.hdf5
Epoch 2/1000
 - 0s - loss: 7293.7832

Epoch 00002: loss did not improve from 3.12757
Epoch 3/1000
 - 0s - loss: 1927.8142

Epoch 00003: loss did not improve from 3.12757
Epoch 4/1000
 - 0s - loss: 1374.9668

Epoch 00004: loss did not improve from 3.12757
Epoch 5/1000
 - 0s - loss: 3262.9243

Epoch 00005: loss did not improve from 3.12757
Epoch 6/1000
 - 0s - loss: 39.3536

Epoch 00006: loss did not improve from 3.12757
Epoch 7/1000
 - 0s - loss: 99.8872

Epoch 00007: loss did not improve from 3.12757
Epoch 8/1000
 - 0s - loss: 5.1030

Epoch 00008: loss did not improve from 3.12757
Epoch 9/1000
 - 0s - loss: 1.5707

Epoch 00009: loss improved from 3.12757 to 1.57073, saving model to weights_best.hdf5
Epoch 10/1000
 - 0s - loss: 1.5923

Epoch 00010: loss did not improve from 1.57073
Epoch 11/1000
 - 0s - loss: 1.8477

Epoch 00011: loss did not improve from 1.57073
Epoch 1